# T81-558: Applications of Deep Neural Networks
* Instructor: [Jeff Heaton](https://sites.wustl.edu/jeffheaton/), School of Engineering and Applied Science, [Washington University in St. Louis](https://engineering.wustl.edu/Programs/Pages/default.aspx)
* For more information visit the [class website](https://sites.wustl.edu/jeffheaton/t81-558/).

**Kaggle Assignment: **

**Student Name: Jason Walker**

# Overview

## Description
This is one of the projects from the course T81-855: Applications of Deep Learning at Washington University in St. Louis. All students must create a Kaggle account and submit a solution. Once you have submitted your solution entry log into Blackboard (at WUSTL) and submit a single file telling me your Kaggle name on the leaderboard (you do not need to register to Kaggle with your real name). This competition will be visible to the public, so there may be non-student submissions as well as student.

The data set for this competition consists of a number of input columns that should be used to predict a stores sales. This is a regression problem. The inputs are a mixture of discrete and category values. The data set is from a simulation.

## Evaluation

The evaluation pages describes how submissions will be scored and how students should format their submissions. The scores are in RMSE.
Submission Format

For every store in the dataset, submission files should contain a sales volume.

The file should contain a header and have the following format:

```
100000,1.23
100001,1.123
100002,3.332
100003,1.53
...
```

# Data

## Data Description

The data contains data and costs for various office supplies. The data came from a simulation and do not directly correspond to any real-world items. See how well you can predict the cost of an item using the provided data. Feature engineering will likely help you. The *name* column may seem useless at first glance; however, it contains information that you can parse to help your predictions.
File descriptions
```
    id - The identifier/primary key.
    name - The name of this item.
    manufacturer - The manufacturer.
    pack - The number of items in this pack.
    weight - The weight of a pack of these items.
    height - The height of a pack of these items.
    width - The width of a pack of these items.
    length - The length of a pack of these items.
    cost - The cost for this item pack. This is what you are to predict (the target). 
```

# Helpful Functions

You will see these at the top of every module and assignment.  These are simply a set of reusable functions that we will make use of.  Each of them will be explained as the semester progresses.  They are explained in greater detail as the course progresses.  Class 4 contains a complete overview of these functions.

In [1]:
from sklearn import preprocessing
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import shutil
import os
import requests
import base64


# Encode text values to dummy variables(i.e. [1,0,0],[0,1,0],[0,0,1] for red,green,blue)
def encode_text_dummy(df, name):
    dummies = pd.get_dummies(df[name])
    for x in dummies.columns:
        dummy_name = "{}-{}".format(name, x)
        df[dummy_name] = dummies[x]
    df.drop(name, axis=1, inplace=True)


# Encode text values to a single dummy variable.  The new columns (which do not replace the old) will have a 1
# at every location where the original column (name) matches each of the target_values.  One column is added for
# each target value.
def encode_text_single_dummy(df, name, target_values):
    for tv in target_values:
        l = list(df[name].astype(str))
        l = [1 if str(x) == str(tv) else 0 for x in l]
        name2 = "{}-{}".format(name, tv)
        df[name2] = l


# Encode text values to indexes(i.e. [1],[2],[3] for red,green,blue).
def encode_text_index(df, name):
    le = preprocessing.LabelEncoder()
    df[name] = le.fit_transform(df[name])
    return le.classes_


# Encode a numeric column as zscores
def encode_numeric_zscore(df, name, mean=None, sd=None):
    if mean is None:
        mean = df[name].mean()

    if sd is None:
        sd = df[name].std()

    df[name] = (df[name] - mean) / sd


# Convert all missing values in the specified column to the median
def missing_median(df, name):
    med = df[name].median()
    df[name] = df[name].fillna(med)


# Convert all missing values in the specified column to the default
def missing_default(df, name, default_value):
    df[name] = df[name].fillna(default_value)


# Convert a Pandas dataframe to the x,y inputs that TensorFlow needs
def to_xy(df, target):
    result = []
    for x in df.columns:
        if x != target:
            result.append(x)
    # find out the type of the target column.  Is it really this hard? :(
    target_type = df[target].dtypes
    target_type = target_type[0] if hasattr(target_type, '__iter__') else target_type
    # Encode to int for classification, float otherwise. TensorFlow likes 32 bits.
    if target_type in (np.int64, np.int32):
        # Classification
        dummies = pd.get_dummies(df[target])
        return df.as_matrix(result).astype(np.float32), dummies.as_matrix().astype(np.float32)
    else:
        # Regression
        return df.as_matrix(result).astype(np.float32), df.as_matrix([target]).astype(np.float32)

# Nicely formatted time string
def hms_string(sec_elapsed):
    h = int(sec_elapsed / (60 * 60))
    m = int((sec_elapsed % (60 * 60)) / 60)
    s = sec_elapsed % 60
    return "{}:{:>02}:{:>05.2f}".format(h, m, s)


# Regression chart.
def chart_regression(pred,y,sort=True):
    t = pd.DataFrame({'pred' : pred, 'y' : y.flatten()})
    if sort:
        t.sort_values(by=['y'],inplace=True)
    a = plt.plot(t['y'].tolist(),label='expected')
    b = plt.plot(t['pred'].tolist(),label='prediction')
    plt.ylabel('output')
    plt.legend()
    plt.show()

# Remove all rows where the specified column is +/- sd standard deviations
def remove_outliers(df, name, sd):
    drop_rows = df.index[(np.abs(df[name] - df[name].mean()) >= (sd * df[name].std()))]
    df.drop(drop_rows, axis=0, inplace=True)


# Encode a column to a range between normalized_low and normalized_high.
def encode_numeric_range(df, name, normalized_low=-1, normalized_high=1,
                         data_low=None, data_high=None):
    if data_low is None:
        data_low = min(df[name])
        data_high = max(df[name])

    df[name] = ((df[name] - data_low) / (data_high - data_low)) \
               * (normalized_high - normalized_low) + normalized_low
        
# This function submits an assignment.  You can submit an assignment as much as you like, only the final
# submission counts.  The paramaters are as follows:
# data - Pandas dataframe output.
# key - Your student key that was emailed to you.
# no - The assignment class number, should be 1 through 1.
# source_file - The full path to your Python or IPYNB file.  This must have "_class1" as part of its name.  
# .             The number must match your assignment number.  For example "_class2" for class assignment #2.
def submit(data,key,no,source_file=None):
    if source_file is None and '__file__' not in globals(): raise Exception('Must specify a filename when a Jupyter notebook.')
    if source_file is None: source_file = __file__
    suffix = '_class{}'.format(no)
    if suffix not in source_file: raise Exception('{} must be part of the filename.'.format(suffix))
    with open(source_file, "rb") as image_file:
        encoded_python = base64.b64encode(image_file.read()).decode('ascii')
    ext = os.path.splitext(source_file)[-1].lower()
    if ext not in ['.ipynb','.py']: raise Exception("Source file is {} must be .py or .ipynb".format(ext))
    r = requests.post("https://api.heatonresearch.com/assignment-submit",
        headers={'x-api-key':key}, json={'csv':base64.b64encode(data.to_csv(index=False).encode('ascii')).decode("ascii"),
        'assignment': no, 'ext':ext, 'py':encoded_python})
    if r.status_code == 200:
        print("Success: {}".format(r.text))
    else: print("Failure: {}".format(r.text))

# Kaggle Code

## Load Data and Encode


In [2]:
import os
import re
import sklearn

import pandas as pd
import numpy as np
import tensorflow as tf

from sklearn import metrics
from sklearn.linear_model import LassoCV
from sklearn.model_selection import train_test_split, KFold
from keras.models import Sequential
from keras.layers.core import Dense, Activation, Dropout
from keras.callbacks import EarlyStopping, ModelCheckpoint
from keras import regularizers

path = './data'

filename_test = os.path.join(path,"test.csv")
filename_train = os.path.join(path,"train.csv")
filename_sample = os.path.join(path,"sample.csv")
filename_submit = os.path.join(path,"submit.csv")
filename_checkpoint = os.path.join(path,"checkpoint.hdf5")

df_train = pd.read_csv(filename_train,na_values=['NA','?'])

np.random.seed(42) # Uncomment this line to get the same shuffle each time
df_train = df_train.reindex(np.random.permutation(df_train.index))
df_train.reset_index(inplace=True, drop=True)

# Encode Features

# Remove all rows where the specified column is +/- sd standard deviations
def extract_and_encode_features(df):
    color_regex='(?P<color>red|blue|green|yellow|orange|pink|black|brown|white)'
    df['color'] = df.name.str.extract(color_regex, flags=re.IGNORECASE, expand=False)

    quality_regex='(?P<quality>generic|high\squality)'
    df['quality'] = df.name.str.extract(quality_regex, flags=re.IGNORECASE, expand=False)

    size_regex='(?P<size>tiny|small|medium|large)'
    df['size'] = df.name.str.extract(size_regex, flags=re.IGNORECASE, expand=False)

    item_regex='(?P<item>paperclips|paperweights|ink\spens|pencils|stapler|tablets|thumbtacks|post\sit\snotes)'
    df['item'] = df.name.str.extract(item_regex, flags=re.IGNORECASE, expand=False)
    
    for column in ['pack','weight','height','width','length']:
        missing_median(df,column)
    
    #df.insert(1,'surface_area',(df['height']*df['width']*df['length']).astype(int))
    
    ## encode numeric features
    #for column in ['pack','weight','height','width','length','surface_area']:
    #    encode_numeric_zscore(df,column)

    # encode text/categorical features
    for column in ['manufacturer','color','quality','size','item']:
        encode_text_dummy(df,column)
  
extract_and_encode_features(df_train)

ids_train = df_train['id']
df_train.drop('id',1,inplace=True)

names_train = df_train['name']
df_train.drop('name',1,inplace=True)

x,y = to_xy(df_train,'cost')

# Used before KFold
#x_train, x_test, y_train, y_test = train_test_split(    
#    x, y, test_size=0.25, random_state=45)


/Users/jwalker/anaconda3/lib/python3.6/importlib/_bootstrap.py:219: RuntimeWarning: compiletime version 3.5 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.6
  return f(*args, **kwds)
Using TensorFlow backend.


## Linear Regression (Coefficients)

In [ ]:
# Simple function to evaluate the coefficients of a regression
%matplotlib inline    
from IPython.display import display, HTML    

def report_coef(names,coef,intercept):
    r = pd.DataFrame( { 'coef': coef, 'positive': coef>=0  }, index = names )
    r = r.sort_values(by=['coef'])
    display(r)
    print("Intercept: {}".format(intercept))
    r['coef'].plot(kind='barh', color=r['positive'].map({True: 'b', False: 'r'}))
    
# Create linear regression
regressor = sklearn.linear_model.LinearRegression()

# Fit/train linear regression
regressor.fit(x_train,y_train)
# Predict
pred = regressor.predict(x_test)

# Measure RMSE error.  RMSE is common for regression.
score = np.sqrt(metrics.mean_squared_error(pred,y_test))
print("Final score (RMSE): {}".format(score))

names = list(df_train.columns.values)
names.remove("cost")
print(names)
report_coef(
  names,
  regressor.coef_[0,:],
  regressor.intercept_)

## L1 Regularization (Lasso)

In [ ]:


import sklearn
from sklearn.linear_model import Lasso

# Create linear regression
regressor = Lasso(random_state=0,alpha=0.01)

# Fit/train LASSO
regressor.fit(x_train,y_train)
# Predict
pred = regressor.predict(x_test)

# Measure RMSE error.  RMSE is common for regression.
score = np.sqrt(metrics.mean_squared_error(pred,y_test))
print("Final score (RMSE): {}".format(score))

names = list(df_train.columns.values)
names.remove("cost")
report_coef(
  names,
  regressor.coef_,
  regressor.intercept_)



## L1 Regularization (Plot LassoCV)

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

from sklearn.linear_model import LassoCV
from sklearn.linear_model import Lasso
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_val_score

lasso = Lasso(random_state=42)
alphas = np.logspace(-8, 8, 10)

scores = list()
scores_std = list()

n_folds = 3

for alpha in alphas:
    lasso.alpha = alpha
    this_scores = cross_val_score(lasso, x, y, cv=n_folds, n_jobs=1)
    scores.append(np.mean(this_scores))
    scores_std.append(np.std(this_scores))

scores, scores_std = np.array(scores), np.array(scores_std)

plt.figure().set_size_inches(8, 6)
plt.semilogx(alphas, scores)

# plot error lines showing +/- std. errors of the scores
std_error = scores_std / np.sqrt(n_folds)

plt.semilogx(alphas, scores + std_error, 'b--')
plt.semilogx(alphas, scores - std_error, 'b--')

# alpha=0.2 controls the translucency of the fill color
plt.fill_between(alphas, scores + std_error, scores - std_error, alpha=0.2)

plt.ylabel('CV score +/- std error')
plt.xlabel('alpha')
plt.axhline(np.max(scores), linestyle='--', color='.5')
plt.xlim([alphas[0], alphas[-1]])

## L2 Regularization (Ridge)

In [ ]:
import sklearn
from sklearn.linear_model import Ridge

# Create linear regression
regressor = Ridge(alpha=1)

# Fit/train Ridge
regressor.fit(x_train,y_train)
# Predict
pred = regressor.predict(x_test)

# Measure RMSE error.  RMSE is common for regression.
score = np.sqrt(metrics.mean_squared_error(pred,y_test))
print("Final score (RMSE): {}".format(score))

names = list(df_train.columns.values)
names.remove("cost")

report_coef(
  names,
  regressor.coef_[0,:],
  regressor.intercept_)

## ElasticNet Regularization

In [ ]:
import sklearn
from sklearn.linear_model import ElasticNet

# Create linear regression
regressor = ElasticNet(alpha=0.01, l1_ratio=0.1)

# Fit/train LASSO
regressor.fit(x_train,y_train)
# Predict
pred = regressor.predict(x_test)

# Measure RMSE error.  RMSE is common for regression.
score = np.sqrt(metrics.mean_squared_error(pred,y_test))
print("Final score (RMSE): {}".format(score))

names = list(df_train.columns.values)
names.remove("cost")

report_coef(
  names,
  regressor.coef_,
  regressor.intercept_)

## Generate Training Model

In [3]:
# Cross-Validate
kf = KFold(10)

checkpoint = ModelCheckpoint(filepath=filename_checkpoint, verbose=0, save_best_only=True)

# Turn off KFold
#if (0):
oos_y = []
oos_pred = []
fold = 0
    
for train, test in kf.split(x):
    fold+=1
    print("Fold #{}".format(fold))
        
    x_train = x[train]
    y_train = y[train]
    x_test = x[test]
    y_test = y[test]
    
    model = Sequential()
    model.add(Dense(100, input_dim=x.shape[1], activation='relu')) # Hidden 1
    model.add(Dropout(0.01)) # Dropout Layer 1
    model.add(Dense(50, activation='relu')) # Hidden 2
    #model.add(Dropout(0.10)) # Dropout Layer 2
    model.add(Dense(25, 
                    kernel_regularizer=regularizers.l2(0.01), #L2 regularization
                    activity_regularizer=regularizers.l1(0.01), #L1 Lasso regularization
                    activation='relu')) # Hidden 3 
    model.add(Dense(10, activation='relu')) # Hidden 4
    model.add(Dense(1)) # Output
    model.compile(loss='mean_squared_error', optimizer='adam')
    monitor = EarlyStopping(monitor='val_loss', min_delta=1e-5, patience=1000, verbose=1, mode='auto')
    model.fit(x_train,y_train,validation_data=(x_test,y_test),callbacks=[monitor,checkpoint],verbose=1,epochs=10000)
    
    pred = model.predict(x_test)
    
    oos_y.append(y_test)
    oos_pred.append(pred)        

    # Measure this fold's RMSE
    score = np.sqrt(metrics.mean_squared_error(pred,y_test))
    print("Fold score (RMSE): {}".format(score))


Fold #1
Train on 9000 samples, validate on 1000 samples
Epoch 1/10000
9000/9000 [==============================] - 1s 138us/step - loss: 5458.0354 - val_loss: 4241.9273
Epoch 2/10000
9000/9000 [==============================] - 1s 60us/step - loss: 5064.4058 - val_loss: 4044.1975
Epoch 3/10000
9000/9000 [==============================] - 1s 62us/step - loss: 4629.3710 - val_loss: 4322.8199
Epoch 4/10000
9000/9000 [==============================] - 1s 62us/step - loss: 4456.2242 - val_loss: 4172.8941
Epoch 5/10000
9000/9000 [==============================] - 1s 60us/step - loss: 4372.2131 - val_loss: 3925.6315
Epoch 6/10000
9000/9000 [==============================] - 1s 61us/step - loss: 4293.8797 - val_loss: 3569.9478
Epoch 7/10000
9000/9000 [==============================] - 1s 58us/step - loss: 4139.3576 - val_loss: 3637.9537
Epoch 8/10000
9000/9000 [==============================] - 1s 61us/step - loss: 4064.0955 - val_loss: 3432.6384
Epoch 9/10000
9000/9000 [======================

Epoch 74/10000
9000/9000 [==============================] - 0s 50us/step - loss: 280.9546 - val_loss: 525.1301
Epoch 75/10000
9000/9000 [==============================] - 0s 50us/step - loss: 341.1598 - val_loss: 256.1993
Epoch 76/10000
9000/9000 [==============================] - 0s 50us/step - loss: 355.7536 - val_loss: 468.1011
Epoch 77/10000
9000/9000 [==============================] - 0s 49us/step - loss: 319.3384 - val_loss: 1305.7035
Epoch 78/10000
9000/9000 [==============================] - 0s 53us/step - loss: 415.7550 - val_loss: 328.7968
Epoch 79/10000
9000/9000 [==============================] - 1s 58us/step - loss: 357.4370 - val_loss: 220.4262
Epoch 80/10000
9000/9000 [==============================] - 1s 58us/step - loss: 310.8657 - val_loss: 257.0361
Epoch 81/10000
9000/9000 [==============================] - 1s 69us/step - loss: 333.1323 - val_loss: 626.0393
Epoch 82/10000
9000/9000 [==============================] - 1s 63us/step - loss: 348.3724 - val_loss: 219.2459


9000/9000 [==============================] - 0s 50us/step - loss: 266.1575 - val_loss: 295.2686
Epoch 148/10000
9000/9000 [==============================] - 0s 50us/step - loss: 257.3764 - val_loss: 227.5378
Epoch 149/10000
9000/9000 [==============================] - 0s 49us/step - loss: 252.0156 - val_loss: 209.0194
Epoch 150/10000
9000/9000 [==============================] - 0s 49us/step - loss: 237.5469 - val_loss: 244.4637
Epoch 151/10000
9000/9000 [==============================] - 0s 49us/step - loss: 252.9323 - val_loss: 202.2344
Epoch 152/10000
9000/9000 [==============================] - 0s 48us/step - loss: 227.1342 - val_loss: 241.9240
Epoch 153/10000
9000/9000 [==============================] - 0s 50us/step - loss: 239.1708 - val_loss: 495.0602
Epoch 154/10000
9000/9000 [==============================] - 0s 49us/step - loss: 234.8748 - val_loss: 211.7475
Epoch 155/10000
9000/9000 [==============================] - 0s 51us/step - loss: 210.3394 - val_loss: 244.5555
Epoch 15

9000/9000 [==============================] - 0s 49us/step - loss: 347.6692 - val_loss: 380.9543
Epoch 221/10000
9000/9000 [==============================] - 0s 50us/step - loss: 321.4883 - val_loss: 195.3649
Epoch 222/10000
9000/9000 [==============================] - 0s 49us/step - loss: 256.3934 - val_loss: 436.1743
Epoch 223/10000
9000/9000 [==============================] - 0s 48us/step - loss: 287.8432 - val_loss: 588.6055
Epoch 224/10000
9000/9000 [==============================] - 0s 49us/step - loss: 247.0714 - val_loss: 233.9629
Epoch 225/10000
9000/9000 [==============================] - 0s 49us/step - loss: 208.2057 - val_loss: 223.1036
Epoch 226/10000
9000/9000 [==============================] - 0s 48us/step - loss: 226.4482 - val_loss: 188.5664
Epoch 227/10000
9000/9000 [==============================] - 0s 50us/step - loss: 222.7701 - val_loss: 195.3382
Epoch 228/10000
9000/9000 [==============================] - 0s 49us/step - loss: 225.4745 - val_loss: 412.0301
Epoch 22

9000/9000 [==============================] - 0s 49us/step - loss: 267.1911 - val_loss: 188.6105
Epoch 294/10000
9000/9000 [==============================] - 0s 48us/step - loss: 229.6807 - val_loss: 211.7960
Epoch 295/10000
9000/9000 [==============================] - 0s 48us/step - loss: 205.2060 - val_loss: 172.2459
Epoch 296/10000
9000/9000 [==============================] - 0s 50us/step - loss: 214.4482 - val_loss: 307.6834
Epoch 297/10000
9000/9000 [==============================] - 0s 49us/step - loss: 189.8479 - val_loss: 199.4082
Epoch 298/10000
9000/9000 [==============================] - 0s 51us/step - loss: 403.1904 - val_loss: 319.7645
Epoch 299/10000
9000/9000 [==============================] - 0s 50us/step - loss: 369.1404 - val_loss: 554.0199
Epoch 300/10000
9000/9000 [==============================] - 0s 49us/step - loss: 260.8285 - val_loss: 201.3074
Epoch 301/10000
9000/9000 [==============================] - 0s 48us/step - loss: 228.3176 - val_loss: 279.9626
Epoch 30

...

9000/9000 [==============================] - 1s 60us/step - loss: 154.8244 - val_loss: 115.8888
Epoch 3001/10000
9000/9000 [==============================] - 0s 54us/step - loss: 140.2054 - val_loss: 112.0495
Epoch 3002/10000
9000/9000 [==============================] - 0s 52us/step - loss: 128.4008 - val_loss: 114.8314
Epoch 3003/10000
9000/9000 [==============================] - 0s 54us/step - loss: 134.0532 - val_loss: 141.4057
Epoch 3004/10000
9000/9000 [==============================] - 0s 53us/step - loss: 142.3194 - val_loss: 123.7619
Epoch 3005/10000
9000/9000 [==============================] - 0s 52us/step - loss: 134.2108 - val_loss: 105.9445
Epoch 3006/10000
9000/9000 [==============================] - 0s 53us/step - loss: 142.3184 - val_loss: 112.7179
Epoch 3007/10000
9000/9000 [==============================] - 0s 55us/step - loss: 139.0263 - val_loss: 107.8675
Epoch 3008/10000
9000/9000 [==============================] - 0s 52us/step - loss: 141.2529 - val_loss: 105.1340


9000/9000 [==============================] - 0s 52us/step - loss: 135.7108 - val_loss: 111.8010
Epoch 3073/10000
9000/9000 [==============================] - 0s 55us/step - loss: 131.5895 - val_loss: 104.0342
Epoch 3074/10000
9000/9000 [==============================] - 0s 53us/step - loss: 139.6354 - val_loss: 148.5199
Epoch 3075/10000
9000/9000 [==============================] - 0s 53us/step - loss: 160.4782 - val_loss: 138.8284
Epoch 3076/10000
9000/9000 [==============================] - 0s 53us/step - loss: 141.2140 - val_loss: 111.2736
Epoch 3077/10000
9000/9000 [==============================] - 1s 58us/step - loss: 139.1935 - val_loss: 109.1161
Epoch 3078/10000
9000/9000 [==============================] - 1s 59us/step - loss: 138.0104 - val_loss: 128.1512
Epoch 3079/10000
9000/9000 [==============================] - 1s 69us/step - loss: 137.1582 - val_loss: 106.2038
Epoch 3080/10000
9000/9000 [==============================] - 1s 65us/step - loss: 136.9522 - val_loss: 116.1983


9000/9000 [==============================] - 0s 53us/step - loss: 142.2321 - val_loss: 116.0826
Epoch 3145/10000
9000/9000 [==============================] - 0s 53us/step - loss: 133.0551 - val_loss: 126.6958
Epoch 3146/10000
9000/9000 [==============================] - 0s 55us/step - loss: 135.9057 - val_loss: 124.2228
Epoch 3147/10000
9000/9000 [==============================] - 0s 52us/step - loss: 133.1063 - val_loss: 106.4643
Epoch 3148/10000
9000/9000 [==============================] - 0s 53us/step - loss: 140.3887 - val_loss: 107.0826
Epoch 3149/10000
9000/9000 [==============================] - 0s 54us/step - loss: 137.1666 - val_loss: 114.9229
Epoch 3150/10000
9000/9000 [==============================] - 0s 54us/step - loss: 135.9160 - val_loss: 115.6922
Epoch 3151/10000
9000/9000 [==============================] - 0s 53us/step - loss: 146.2018 - val_loss: 151.1116
Epoch 3152/10000
9000/9000 [==============================] - 0s 53us/step - loss: 148.7990 - val_loss: 124.9962


9000/9000 [==============================] - 0s 53us/step - loss: 136.1133 - val_loss: 113.9993
Epoch 3217/10000
9000/9000 [==============================] - 0s 52us/step - loss: 145.9423 - val_loss: 108.8793
Epoch 3218/10000
9000/9000 [==============================] - 0s 53us/step - loss: 144.3357 - val_loss: 117.8846
Epoch 3219/10000
9000/9000 [==============================] - 0s 52us/step - loss: 151.2660 - val_loss: 128.6676
Epoch 3220/10000
9000/9000 [==============================] - 0s 54us/step - loss: 170.1727 - val_loss: 163.7665
Epoch 3221/10000
9000/9000 [==============================] - 0s 53us/step - loss: 155.9056 - val_loss: 123.2857
Epoch 3222/10000
9000/9000 [==============================] - 0s 53us/step - loss: 142.6093 - val_loss: 131.6196
Epoch 3223/10000
9000/9000 [==============================] - 0s 52us/step - loss: 134.9350 - val_loss: 113.0689
Epoch 3224/10000
9000/9000 [==============================] - 0s 53us/step - loss: 140.1761 - val_loss: 122.4190


9000/9000 [==============================] - 0s 53us/step - loss: 139.7158 - val_loss: 125.5386
Epoch 3289/10000
9000/9000 [==============================] - 0s 53us/step - loss: 134.1427 - val_loss: 105.3505
Epoch 3290/10000
9000/9000 [==============================] - 0s 52us/step - loss: 131.1725 - val_loss: 117.4265
Epoch 3291/10000
9000/9000 [==============================] - 0s 53us/step - loss: 140.4310 - val_loss: 118.7554
Epoch 3292/10000
9000/9000 [==============================] - 0s 53us/step - loss: 134.6182 - val_loss: 122.1325
Epoch 3293/10000
9000/9000 [==============================] - 0s 51us/step - loss: 147.0792 - val_loss: 116.8677
Epoch 3294/10000
9000/9000 [==============================] - 0s 53us/step - loss: 133.2187 - val_loss: 155.8163
Epoch 3295/10000
9000/9000 [==============================] - 0s 53us/step - loss: 177.4163 - val_loss: 132.4522
Epoch 3296/10000
9000/9000 [==============================] - 1s 56us/step - loss: 143.8263 - val_loss: 106.5045


## Out-of-sample RMSE

In [ ]:
# Build the oos prediction list and calculate the error.
oos_y = np.concatenate(oos_y)
oos_pred = np.concatenate(oos_pred)
score = np.sqrt(metrics.mean_squared_error(oos_pred,oos_y))
print("Final, out of sample score (RMSE): {}".format(score)) 

In [ ]:

#pred = model.predict(x_test)

# Measure RMSE error.  RMSE is common for regression.
#score = np.sqrt(metrics.mean_squared_error(pred,y_test))
#print("Final score (RMSE): {}".format(score))

#chart_regression(pred.flatten(),y_test)
#chart_regression(pred.flatten(),y_test,sort=False)

## Load Best Weights and Predict on Test

In [ ]:
model.load_weights(filename_checkpoint)

df_test = pd.read_csv(filename_test,na_values=['NA','?'])

extract_and_encode_features(df_test)

ids_test = df_test['id']
df_test.drop('id',1,inplace=True)

names_test = df_test['name']
df_test.drop('name',1,inplace=True)

x_submit = df_test.as_matrix().astype(np.float32)
pred_submit = model.predict(x_submit)

# Handles negative cost values. Use inverse
cost = [n if n > 0 else n * -1 for n in pred_submit[:,0]]

df_submit = pd.DataFrame({'id': ids_test,'cost': cost})
df_submit = df_submit[['id', 'cost']]
df_submit.to_csv(filename_submit, index=False)